# Simulation ,Estimation, and Forecasting of GARCH
*--What are we talking about when we talk about fit?*
<br>
*Kaiyi Li<br>
YUjia Dong<br>
Yundie Ma<br>*


This project aims to find out the reasoning for the estimation of GARCH model. 
First, we simulate a GARCH(1,1) process with arbitrary parameters. Then we illustrate how to fit the model with MLE and GMM.
Then we compare the parameters from the fitted result to the arbitraged one. Then we apply them to empircal data. 
## Project Initiatialization
Before start, we publish all our graphs on plotly and load our libraries.


In [219]:
from functools import partial
import math
import numpy as np
import scipy
from scipy import stats
import statsmodels.api as sm
from statsmodels.stats.stattools import jarque_bera
import chart_studio
import plotly.graph_objects as go
import chart_studio.plotly as py
import pandas as pd
import plotly
chart_studio.tools.set_credentials_file(username='Kaiyi', api_key='M1B4Wl1YvQQHigAZntyo')


## Simulate a GARCH process
### Setting parameters

$$
\sigma_t^2 = \omega+\alpha r_{t-1}^2+\beta \sigma^2_{t-1}\\
r_t = \sigma_t \epsilon_t \\
\epsilon_{t} \sim \mathcal{N}(0,1)\\
$$
We set the parameters as following: 
$$
\omega = 1\\
\alpha = 0.3\\
\beta = 0.5\\
\sigma_0 = \sqrt{\frac{1}{1-\alpha-\beta}}
$$
Create 11000 points, drop first 1000 as burn-in.

In [23]:
#Set our parameters and initial sigma.
omega = 1
alpha = 0.3
beta = 0.5
sigma_zero = math.sqrt(1/(1-alpha-beta))
N = 10000

### Simulate a GARCH(1,1) Process

In [32]:
#N is the length of the process
def simulate_garch(N,omega,alpha,beta,burn_in_ratio=0.1):
    #Size of burin in.
    burn_in = int(burn_in_ratio*N)
    #Create an array of r_t
    r_t = np.ndarray(N+burn_in)
    #Create an array of sigmas.
    sigmas = np.ndarray(N+burn_in)
    #Set initial Sigma
    sigmas[0] = sigma_zero
    #Start Simulation
    for t in range(1,N+burn_in):
        #Create a random variable from a standard normal distribution as epsilon.
        epsilon = np.random.normal(0,1)
        #Create a r_t
        r_t[t-1] = sigmas[t-1]*epsilon
        #Create a sigma_t
        sigmas[t] = math.sqrt(omega+alpha*r_t[t-1]**2+beta*sigmas[t-1]**2)
    #Drop the burn in. 
    sigmas = sigmas[burn_in:]
    r_t = r_t[burn_in:]
    simulation_result = pd.DataFrame(data = {'r':r_t, 'sigmas':sigmas},index = np.arange(N))
    #Write the simulation_result on the disk.
    simulation_result.to_csv('simulation_result.csv')
    return sigmas,r_t,simulation_result
sigmas,r_t,simulation_result=simulate_garch(N,omega,alpha,beta,burn_in_ratio=0.1)

Let's take a look at the simulation result.

In [39]:
simulation_plots = go.Figure()
simulation_plots.add_trace(go.Scatter(x=simulation_result.index, y=simulation_result['r']))
simulation_plots.update_layout(title='Simulation of GARCH(1,1): R',
                   xaxis_title='simulation index',
                   yaxis_title='r')
simulation_plots.show()
# Upstream the graph to chart_studio
# py.plot(simulation_plots,filename='simulation_of_r',autO_open = True)
# Save the graph in html
# plotly.offline.plot(fig, filename='plots/simulated_r.html')

In [133]:
simulation_plots = go.Figure()
simulation_plots.add_trace(go.Scatter(x=simulation_result.index, y=simulation_result['sigmas'],line = dict(color='orange')))
simulation_plots.update_layout(title='Simulation of GARCH(1,1): Sigma',
                   xaxis_title='simulation index',
                   yaxis_title=r'$\sigma$')
simulation_plots.show()
# Upstream the graph to chart_studio
# py.plot(simulation_plots,filename='simulation_of_sigma',autO_open = True)
# Save the graph in html
# plotly.offline.plot(fig, filename='plots/simulated_r.html')

## Estimate a GARCH(1,1) Process
Before Estimation, let's estimate the simulated result in R and see its estimation as our benchmark. 

This is the r fitted result (using rugarch)

|Parameter| Estimate| Std.Error| t value
|---------|---------|----------|--------
|omega  |  1.04821 |   0.073430|   14.275        
|alpha1 | 0.31275  |  0.016500 |  18.954        
|beta1  |  0.48461 |   0.023088|   20.990        



### Maximum Likelihood Estimation
#### Derieve the negative loglikelihood function of GARCH(1,1)
First, we derieve the likelihood of GARCH(1,1)
$$
r \sim \mathcal{N}(0,\sigma_t^2)\\
\theta = [\omega,\alpha,\beta]\\
f(r_0,r_1,\cdots ,r_t;\theta) = f(r_0;\theta)f(r_t|r_{t-1},\cdots, r_1;\theta)\\
=f(r_0;\theta)f(r_t|r_{t-1},\cdots, r_1;\theta)\\
=f(r_0;\theta)\Pi_{t=1}^{T} f(r_t|R_{t-1};\theta)\\
=f(r_0;\theta)\Pi_{t=1}^{T} \frac{1}{\sqrt{2\pi\sigma_t^2}}exp(-\frac{r_t^2}{2\sigma_t^2})\\
$$
<br>
Then we drop the first term $f(r_0;\theta)$ because it is a constant, and then take a log, then we have the log-likelihood function:
<br>
$$
\mathcal{L}(\theta) = \sum_{t=1}^{T} -\frac{1}{2} [ln(2\pi)+ln(\sigma_t^2) +\frac{r_t^2}{\sigma_t^2}]
$$
<br>
After we have the log-likelihood function, our objective would be find a vector $\hat\theta$ that can maximize $\mathcal{L(\theta)}$. 
<br>
$$
\hat\theta = \underset{\theta}{\operatorname{argmax}} \mathcal{L}(\theta) = \underset{\theta}{\operatorname{argmin}}-\mathcal{L}(\theta)
$$ 

In [76]:
#We will need a function that could generate the sigma squares given the initial guess. 
def sigma_squares_calculation(r_t,initial_sigma,theta):
    #unpack the theta
    omega = theta[0]
    alpha = theta[1]
    beta = theta[2]
    #Create the list to store the calculated version of sigma squares. 
    T = len(r_t)
    sigma_squares = np.ndarray(T)
    sigma_squares[0] = initial_sigma**2
    #Store the calculated sigma squares.
    for t in range(1,T):
        sigma_square = omega+alpha*r_t[t-1]**2+beta*sigmas[t-1]**2    
        sigma_squares[t] = sigma_square
#         print(sigma_squares)
    return sigma_squares

The negative log-likelihood function.
$$-\mathcal{L}(\theta) = \sum_{t=1}^{T} \frac{1}{2} [ln(2\pi)+ln(\sigma_t^2) +\frac{r_t^2}{\sigma_t^2}]$$

In [113]:
def negative_log_likelihood_for_garch(r_t,theta):
    T = len(r_t)
    
    #Estimate the initial sigma.
    initial_sigma = np.sqrt(np.mean(r_t ** 2))
    
    #Calculate the sigma squares
    sigma_squares = sigma_squares_calculation(r_t, initial_sigma, theta)
    
    #Calculate the negative log likelihood.
    negative_log_likelihood = 0
    for t in range(T):
        negative_log_likelihood += (np.log(2*np.pi)+np.log(sigma_squares[t])+(r_t[t]**2)/sigma_squares[t])/2
    
    return negative_log_likelihood

# negative_log_likelihood_for_garch(r_t,theta)

21548.72941350124

#### Find the $\theta$  that minimize the negative log-likelihood.
The Minimization problem is formulated as below:<br>
$$obj: \sum_{t=1}^{T} \frac{1}{2} [ln(2\pi)+ln(\sigma_t^2) +\frac{r_t^2}{\sigma_t^2}]\\
cons:\\
\alpha >0\\
      \beta > 0\\
      -\alpha - \beta \ge -1
$$


In [114]:
#Initial guess
# theta = np.array([0.5,0.5,0.5])
#Define the objective function
objective = partial(negative_log_likelihood_for_garch,r_t)
#Define constraints
def constraint1(theta):return np.array([1-(theta[1]+theta[2])]) 
def constraint2(theta):return np.array([theta[1]]) 
def constraint3(theta):return np.array([theta[2]])

cons = ({'type': 'ineq', 'fun': constraint1},
        {'type': 'ineq', 'fun': constraint2},
        {'type': 'ineq', 'fun': constraint3})
#Result
result = scipy.optimize.minimize(objective,(1,0.5,0.5),method = 'SLSQP',constraints = cons)

/Users/likaiyi/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:28: RuntimeWarning:

invalid value encountered in log



In [116]:
hat_theta_MLE = result.x
hat_theta_MLE

array([1.01926617, 0.31005613, 0.49917752])

$$\hat{\theta}_{MLE} = [1.01926617, 0.31005613, 0.49917752]$$

### General Method of Moments 
Due to the recursive nature of GARCH,which makes it really hard to estimate GARCH parameters using GMM, therefore MLE is usually favoured over GMM. Here we try GMM.<br>
We use four moments for this GMM estimation.
$$
\hat{\epsilon} = \frac{r_t}{\sigma_t}\\
Var(\epsilon) = (\epsilon_t)^2\\
Skew(\epsilon) = (\frac{\epsilon_t - E(\epsilon_t)^3}{\sigma_t^3})\\
Kurtosis(\epsilon) = \frac{(\epsilon_t - E(\epsilon_t))^4}{\sigma_t^4}\\
$$
Start with an identity matrix *W_0* and estimate a $\theta$ to minimize the object below:
$$
\min_{\theta \in \Theta} \left(\frac{1}{T} \sum_{t=1}^T g(r_t, \hat\theta)\right)' W_0 \left(\frac{1}{T}\sum_{t=1}^T g(r_t, \hat\theta)\right)
$$
Define the function to calculate the objective. <br>
Calculate the covariance matrix of g as next W so we could focus more on parameters that gives more explanatory power.<br>

In [178]:
def standardized_moment(r, mu, sigma, n):
    return ((r - mu) ** n) / (sigma ** n)
def gmm_objective(r_t, W, theta):
    # Compute the residuals for X and theta
    initial_sigma = np.sqrt(np.mean(r_t ** 2))
    sigma = np.sqrt(sigma_squares_calculation(r_t, initial_sigma, theta))
    e = r_t / sigma
    
    # Compute the mean moments
    m1 = np.mean(e)
    m2 = np.mean(e ** 2) - 1
    m3 = np.mean(standardized_moment(e, np.mean(e), np.std(e), 3))
    m4 = np.mean(standardized_moment(e, np.mean(e), np.std(e), 4) - 3)
    
    G = np.matrix([m1, m2, m3, m4]).T
    
    return np.asscalar(G.T * W * G)

def gmm_variance(r_t, theta):
    # Compute the residuals for X and theta    
    initial_sigma = np.sqrt(np.mean(r_t ** 2))
    sigma = np.sqrt(sigma_squares_calculation(r_t, initial_sigma, theta))
    e = r_t / sigma

    # Compute the squared moments
    m1 = e ** 2
    m2 = (e ** 2 - 1) ** 2
    m3 = standardized_moment(e, np.mean(e), np.std(e), 3) ** 2
    m4 = (standardized_moment(e, np.mean(e), np.std(e), 4) - 3) ** 2
    
    # Compute the covariance matrix g * g'
    T = len(r_t)
    s = np.ndarray((4, 1))
    for t in range(T):
        G = np.matrix([m1[t], m2[t], m3[t], m4[t]]).T
        s = s + G * G.T
    
    return s / T

#### Start The Iteration

In [188]:
#First, initial W as I.
W = np.identity(4)
number_of_gmm_iterations = 5
#First Guess
hat_theta_GMM = hat_theta_MLE
# theta_gmm_hat = (0.9,0.5,0.5)
#Iteration
for i in range(number_of_gmm_iterations):
    #Estimate New Theta by minimizing the objective.
    objective = partial(gmm_objective,r_t,W)
    result = scipy.optimize.minimize(objective,hat_theta_GMM,constraints = cons)
    hat_theta_GMM = result.x
    print("Iteration"+str(i+1)+":"+str(hat_theta_GMM))
#     gmm_objective(r_t,W,theta_gmm_hat)
    #Recompute W.
    W = np.linalg.inv(gmm_variance(r_t,hat_theta_GMM))

/Users/likaiyi/opt/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:17: DeprecationWarning:

np.asscalar(a) is deprecated since NumPy v1.16, use a.item() instead



Iteration1:[1.01897988 0.309648   0.50011487]
Iteration2:[1.01931932 0.31056988 0.50148609]
Iteration3:[1.01931932 0.31056988 0.50148609]
Iteration4:[1.01931932 0.31056988 0.50148609]
Iteration5:[1.01931932 0.31056988 0.50148609]


## Model Comparison

In [198]:
# #Now, let's compare the result. 
# ## Let's plot the result of true sigma, MLE estimated sigma, and GMMM estimated sigma.
initial_sigma = np.sqrt(np.mean(r_t ** 2))
GMM_estimated_sigma = np.sqrt(sigma_squares_calculation(r_t, initial_sigma, hat_theta_GMM))
MLE_estimated_sigma = np.sqrt(sigma_squares_calculation(r_t,initial_sigma,hat_theta_MLE))
r_estimated_sigma = np.sqrt(sigma_squares_calculation(r_t,initial_sigma,(1.0481,0.31275,0.48461)))

In [199]:
estimation_plots = go.Figure()
estimation_plots.add_trace(go.Scatter(x=simulation_result.index, y=simulation_result['sigmas'],line = dict(color='orange'),name = "True"))
estimation_plots.add_trace(go.Scatter(x=simulation_result.index, y=GMM_estimated_sigma,line = dict(color='blue'),name = "GMM"))
estimation_plots.add_trace(go.Scatter(x=simulation_result.index, y=MLE_estimated_sigma,line = dict(color='red'),name = "MLE"))
estimation_plots.add_trace(go.Scatter(x=simulation_result.index, y=r_estimated_sigma,line = dict(color='black'),name = "R"))

estimation_plots.update_layout(title='Estimations of GARCH(1,1): Sigma',
                   xaxis_title='simulation index',
                   yaxis_title=r'$\sigma$')
estimation_plots.show()
# Upstream the graph to chart_studio
# py.plot(estimation_plots,filename='Estimations_of_sigma',autO_open = True)
# Save the graph in html
# plotly.offline.plot(fig, filename='estimations.html')

In [208]:
#Calculate the difference between.
MLE_diff = (sum(MLE_estimated_sigma-sigmas))**2/N
GMM_diff = (sum(GMM_estimated_sigma-sigmas))**2/N
r_diff = (sum(r_estimated_sigma-sigmas))**2/N
print("Deviations from MLE estimation:"+str(MLE_diff))
print("Deviations from GMM estimation:"+str(GMM_diff))
print("Deviations from R estimation:"+str(r_diff))

Deviations from MLE estimation:1.6142428711514296
Deviations from GMM estimation:2.4654340250139803
Deviations from R estimation:0.3940689531452904


MLE result is better than GMM. However, we only run one simulation, to get a more soundful result comparison between GMM and MLE, we should probably repeat this process for much more iterations. The difference betwee R's estimation and MLE's estimation, might resulted from **simulation error.** But it might also resulted from the difference between MLE and QMLE.

## Empircal Data
Now let's use MLE,GMM for real world empircal data: SP500. And compared our estimation with VIX.

In [214]:
#Load the data.
GSPC = pd.read_csv('GSPC.csv')[['Date','Open','High','Low','Close','Adj Close']]
GSPC['DATE'] = pd.to_datetime(GSPC['Date'],format='%Y-%m-%d')
GSPC = GSPC[['DATE','Open','High','Low','Close','Adj Close']]
GSPC.set_index('DATE', inplace=True)
VIX = pd.read_csv('VIX.csv')[['Date','Open','High','Low','Close','Adj Close']]
VIX['DATE'] = pd.to_datetime(VIX['Date'],format='%Y-%m-%d')
VIX = VIX[['DATE','Open','High','Low','Close','Adj Close']]
VIX.set_index('DATE', inplace=True)

In [220]:
fig = go.Figure(data=[go.Candlestick(
    x=GSPC.index,
    open=GSPC['Open'], high=GSPC['High'],
    low=GSPC['Low'], close=GSPC['Adj Close'],
    increasing_line_color= 'green', decreasing_line_color= 'red'
)])
fig.show()
# plotly.offline.plot(fig, filename='GSPC.html')

'GSPC.html'

In [221]:
fig = go.Figure(data=[go.Candlestick(
    x=VIX.index,
    open=VIX['Open'], high=VIX['High'],
    low=VIX['Low'], close=VIX['Adj Close'],
    increasing_line_color= 'green', decreasing_line_color= 'red'
)])
fig.show()
# plotly.offline.plot(fig, filename='VIX.html')

'VIX.html'

In [222]:
gspc_rs = np.diff(np.log(GSPC['Close']))
gspc_return_plots = go.Figure()
gspc_return_plots.add_trace(go.Scatter(x=GSPC.index[1:], y=gspc_rs))
gspc_return_plots.update_layout(title='Simulation of GARCH(1,1): R',
                   xaxis_title='simulation index',
                   yaxis_title='r')
gspc_return_plots.show()